# dialogpt가 뭔데

In [1]:
from transformers import AutoModelForCausalLM, AutoTokenizer
import torch

tokenizer = AutoTokenizer.from_pretrained("microsoft/DialoGPT-medium", padding_side="left")
model = AutoModelForCausalLM.from_pretrained("microsoft/DialoGPT-medium")
model = model.eval()


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching /usr/local/cuda/lib64...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 6.1
CUDA SETUP: Detected CUDA version 111
CUDA SETUP: Loading binary /home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/libbitsandbytes_cuda111_nocublaslt.so...


/home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /home/wooseok/miniconda3/envs/peft did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
/home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('F2=\\E[24~'), PosixPath('k8=\\E[19~'), PosixPath('st=\\EH'), PosixPath('so=\\E'), PosixPath('AF=\\E[3%dm'), PosixPath('le=^H'), PosixPath('*7=\\E[1;2F'), PosixPath('cl=\\E[H\\E[J'), PosixPath('dl=\\E[M'), PosixPath('Km=\\E[M'), PosixPath('SC|screen.xterm-256color|VT 100/ANSI X3.64 virtual terminal'), PosixPath('bt=\\E[Z'), PosixPath('cm=\\E[%i%d;%dH'), PosixPath('F3=\\E[1;2P'), PosixPath('@7=\\E[4~'), PosixPath('#4=\\E[1;2D'), PosixPath('me=\\E[m'), PosixPath('DC=\\E[%dP'), PosixPath('%i=\\E[1;2C'), PosixPath('bl=^G'), PosixPath('ue=\\E'), PosixPath('kd=\\EO

In [3]:
model.to('cuda')

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 1024)
    (wpe): Embedding(1024, 1024)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-23): 24 x GPT2Block(
        (ln_1): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=1024, out_features=50257, bias=False)
)

In [3]:
import torch
print(torch.__version__)

1.10.0


In [4]:
patient_utters = ["hi","how are you?","fuck you bro"]
 
for step, PU in enumerate(patient_utters):
    # encode the new user input, add the eos_token and return a tensor in Pytorch
    new_user_input_ids = tokenizer.encode(PU + tokenizer.eos_token, return_tensors='pt')
    print("patient: {}".format(PU))
    
    # append the new user input tokens to the chat history
    bot_input_ids = torch.cat([chat_history_ids, new_user_input_ids], dim=-1) if step > 0 else new_user_input_ids

    # generated a response while limiting the total chat history to 1000 tokens, 
    chat_history_ids = model.generate(bot_input_ids, max_length=1000, pad_token_id=tokenizer.eos_token_id)
    ##print(chat_history_ids)
    # pretty print last ouput tokens from bot
    print("Doctor(Dialogpt): {}".format(tokenizer.decode(chat_history_ids[:, bot_input_ids.shape[-1]:][0], skip_special_tokens=True)))


A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


patient: hi


A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


Doctor(Dialogpt): Hey! :D
patient: how are you?


A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


Doctor(Dialogpt): I'm good, how are you?
patient: fuck you bro
Doctor(Dialogpt): I'm sorry, I'm not your bro.


# 하윤이 데이터로 추론해보기

In [1]:
import numpy as np
import tempfile
from datasets import load_dataset
from transformers import GPT2Tokenizer, GPT2LMHeadModel, TrainingArguments, Trainer
import pandas as pd
import datasets
from datasets import DatasetDict
import json
with open('/home/wooseok/bibm/IMCS21_json/IMCS21_json/train_trans.json') as f:
    data_train = json.load(f)
with open('/home/wooseok/bibm/IMCS21_json/IMCS21_json/test_trans.json') as f:
    data_test = json.load(f)
with open('/home/wooseok/bibm/IMCS21_json/IMCS21_json/dev_trans.json') as f:
    data_val = json.load(f)

<frozen importlib._bootstrap>:219: RuntimeWarning: pyarrow._fs.FileInfo size changed, may indicate binary incompatibility. Expected 64 from C header, got 88 from PyObject
<frozen importlib._bootstrap>:219: RuntimeWarning: pyarrow._fs.FileSelector size changed, may indicate binary incompatibility. Expected 48 from C header, got 72 from PyObject



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching /usr/local/cuda/lib64...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 6.1
CUDA SETUP: Detected CUDA version 111
CUDA SETUP: Loading binary /home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/libbitsandbytes_cuda111_nocublaslt.so...


/home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: /home/wooseok/miniconda3/envs/peft did not contain libcudart.so as expected! Searching further paths...
  warn(msg)
/home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('cd=\\E[J'), PosixPath('kR=\\E[1;2A'), PosixPath('op=\\E'), PosixPath('DO=\\E[%dB'), PosixPath('co#120'), PosixPath('%c=\\E[6;2~'), PosixPath('dc=\\E[P'), PosixPath('%i=\\E[1;2C'), PosixPath('RI=\\E[%dC'), PosixPath('ku=\\EOA'), PosixPath('kd=\\EOB'), PosixPath('sr=\\EM'), PosixPath('AL=\\E[%dL'), PosixPath('k1=\\EOP'), PosixPath('st=\\EH'), PosixPath('AB=\\E[4%dm'), PosixPath('k9=\\E[20~'), PosixPath('F2=\\E[24~'), PosixPath('mi'), PosixPath('ue=\\E'), PosixPath('nd=\\E[C'), PosixPath('up=\\EM'), PosixPath('dl=\\E[M'), PosixPath('al=\\E[L'), PosixPath('*4=\\

In [2]:
data_train

{'0': {'diagnosis': "Children's indigestion",
  'dialogue': [{'sentence_id': '1', 'speaker': 'doctor', 'sentence': 'Hello'},
   {'sentence_id': '2', 'speaker': 'doctor', 'sentence': 'Are you there'},
   {'sentence_id': '3',
    'speaker': 'patient',
    'sentence': 'Is this Baba normal?'},
   {'sentence_id': '4',
    'speaker': 'doctor',
    'sentence': 'From the pictures you posted, the child’s stool is a bit sparse, and there are mucus in the stool'},
   {'sentence_id': '5',
    'speaker': 'patient',
    'sentence': 'If the abnormal, is it related to the milk powder you eat?'},
   {'sentence_id': '6',
    'speaker': 'doctor',
    'sentence': 'The main problem is that there are mucus in the stool, and a routine inspection of the stool needs to be performed.'},
   {'sentence_id': '7',
    'speaker': 'doctor',
    'sentence': 'The relationship with milk powder is not particularly big'},
   {'sentence_id': '8',
    'speaker': 'doctor',
    'sentence': 'How long has this child used this m

In [ ]:
dataset = data_test

# Initialize an empty list to store patient's utterances
patient_dialogues = []

# Iterate through each dialogue in the dataset
for dialogue_id, dialogue_info in dataset.items():
    # Extract the diagnosis information (optional, you can remove this line if not needed)
    diagnosis = dialogue_info['diagnosis']
    
    # Extract the list of dialogue sentences
    sentences = dialogue_info['dialogue']
    
    # Initialize an empty list to store patient's sentences in this dialogue
    patient_sentences = []
    
    # Iterate through each sentence in the dialogue
    for sentence_info in sentences:
        speaker = sentence_info['speaker']
        sentence = sentence_info['sentence']
        
        # Check if the speaker is 'patient', and if yes, add the sentence to the patient's sentences list
        if speaker == 'patient':
            patient_sentences.append(sentence)
    
    # Append the patient's sentences for this dialogue to the patient_dialogues list
    if patient_sentences:
        patient_dialogues.append(patient_sentences)

# patient_dialogues will now contain 811 dialogues consisting only of patient's utterances


In [ ]:
patient_dialogues[0]

In [ ]:
patient_utters = patient_dialogues[0]
 
for step, PU in enumerate(patient_utters):
    # encode the new user input, add the eos_token and return a tensor in Pytorch
    new_user_input_ids = tokenizer.encode(PU + tokenizer.eos_token, return_tensors='pt')
    print("patient: {}".format(PU))
    # append the new user input tokens to the chat history
    bot_input_ids = torch.cat([chat_history_ids, new_user_input_ids], dim=-1) if step > 0 else new_user_input_ids

    # generated a response while limiting the total chat history to 1000 tokens, 
    chat_history_ids = model.generate(bot_input_ids, max_length=10000, pad_token_id=tokenizer.eos_token_id)
    ##print(chat_history_ids)
    # pretty print last ouput tokens from bot
    print("patient: {}".format(tokenizer.decode(chat_history_ids[:, bot_input_ids.shape[-1]:][0], skip_special_tokens=True)))


# covid19 데이터로 파인튜닝

## dataset 전처리

In [1]:
import re
import pickle
import random

In [2]:
dialogues_texts_dirty = open('data/english/COVID-Dialogue-Dataset-English.txt').read().split('id=')
print(len(dialogues_texts_dirty))
print(dialogues_texts_dirty[1])

606
1
https://www.icliniq.com/qa/covid-19/i-have-cough-with-no-travel-history-is-this-a-symptoms-of-covid-19

Description
I have cough with no travel history. Is this a symptom of Covid-19?

Dialogue
Patient:
Hello doctor, I get a cough for the last few days, which is heavy during night times. No raise in temperature but feeling tired with no travel history. No contact with any Covid-19 persons. It has been four to five days and has drunk a lot of Benadryl and took Paracetamol too. Doctors have shut the OP so do not know what to do? Please help.
Doctor:
Hello, I understand your concern. I just have a few more questions.
Does your cough has phlegm? Any other symptoms like difficulty breathing? Any other medical condition such as asthma, hypertension? Are you a smoker? Alcoholic beverage drinker?
Patient:
Thank you doctor,
I have phlegm but not a lot. A tiny amount comes out most of the time. I have no difficulty in breathing. No medical conditions and not a smoker nor a drinker.
Doctor:

In [3]:
cleantext = lambda text: re.sub('\s+', ' ', text).lower().strip()

dialogues = []
for i, text in enumerate(dialogues_texts_dirty):
    text = text[text.find('Description'):].strip()

    description = text[len('Description\n'):text.find('\nDialogue')]
    description = cleantext(description)
    
    text = text[text.find('\nPatient:'):]
    
    utterances, last_person, valid = [], 'None', True
    for x in re.finditer('Doctor:|Patient:', text):
        if x.group() == last_person:
            valid = False
            #print(i)
            break
        else:
            last_person = x.group()

        utterance = text[x.end():].split('Patient:')[0].split('Doctor:')[0]
        utterances.append(cleantext(utterance))

    if valid and utterances:
        dialogues.append({
            'description': description,
            'utterances': utterances
        })

print('#dialogs:', len(dialogues))
print(dialogues[0])

#dialogs: 603
{'description': 'i have cough with no travel history. is this a symptom of covid-19?', 'utterances': ['hello doctor, i get a cough for the last few days, which is heavy during night times. no raise in temperature but feeling tired with no travel history. no contact with any covid-19 persons. it has been four to five days and has drunk a lot of benadryl and took paracetamol too. doctors have shut the op so do not know what to do? please help.', 'hello, i understand your concern. i just have a few more questions. does your cough has phlegm? any other symptoms like difficulty breathing? any other medical condition such as asthma, hypertension? are you a smoker? alcoholic beverage drinker?', 'thank you doctor, i have phlegm but not a lot. a tiny amount comes out most of the time. i have no difficulty in breathing. no medical conditions and not a smoker nor a drinker.', 'hi, i would recommend you take n-acetylcysteine 200 mg powder dissolved in water three times a day. you may

In [6]:
dialogues[:2]

[{'description': 'i have cough with no travel history. is this a symptom of covid-19?',
  'utterances': ['hello doctor, i get a cough for the last few days, which is heavy during night times. no raise in temperature but feeling tired with no travel history. no contact with any covid-19 persons. it has been four to five days and has drunk a lot of benadryl and took paracetamol too. doctors have shut the op so do not know what to do? please help.',
   'hello, i understand your concern. i just have a few more questions. does your cough has phlegm? any other symptoms like difficulty breathing? any other medical condition such as asthma, hypertension? are you a smoker? alcoholic beverage drinker?',
   'thank you doctor, i have phlegm but not a lot. a tiny amount comes out most of the time. i have no difficulty in breathing. no medical conditions and not a smoker nor a drinker.',
   'hi, i would recommend you take n-acetylcysteine 200 mg powder dissolved in water three times a day. you may a

### train, dev, test pickle 파일로 저장

In [5]:
random.seed(11111)
random.shuffle(dialogues)

train_size = int(0.8 * len(dialogues))
dev_size = int(0.1 * len(dialogues))

pickle.dump(dialogues[:train_size],
            open(f'data/english/train.pickle', 'wb'))
pickle.dump(dialogues[train_size:train_size + dev_size],
            open(f'data/english/dev.pickle', 'wb'))
pickle.dump(dialogues[train_size + dev_size:],
            open(f'data/english/test.pickle', 'wb'))

## Finetuning

### training dataset 준비 
- datasets dictionary 만들기 

In [7]:
def load_data(split):
    examples = pickle.load(open(f'data/english/{split}.pickle', 'rb'))

    dialogues = []
    for example in examples:
        dialogues.append(example['utterances'])

    return dialogues

max_length=1024
datasets = {}
model_size = 'small'
from transformers import AutoTokenizer
from collections import namedtuple
tokenizer = AutoTokenizer.from_pretrained(f"microsoft/DialoGPT-{model_size}")
TextDataExample = namedtuple('TextDataExample', ['dialogue', 'tokens', 'mask'])

for split in ['train', 'dev','test']:
    #split = 'train'
    dialogues = load_data(split) # utterances 만 뽑아왔음 
    #print(len(dialogues))
    #print(dialogues[0])
    #print(" -----------------------------")

    datasets[split]=[]
    for dialogue in dialogues:
        tokens, mask = [], []
        for i, utterance in enumerate(dialogue):
            token_ids = tokenizer.encode(utterance + tokenizer.eos_token)
            tokens.extend(token_ids)
            mask.extend([i % 2] * len(token_ids)) 
            '''
            i =0 -> [0] 처음에 환자일 때, 환자의 token 수만큼 0, 
            i=1 -> [1] doctor의 token 수만큼 1 
            '''
        tokens = tokens[:max_length]
        mask = mask[:max_length]

        datasets[split].append(TextDataExample(
            dialogue=dialogue, tokens=tokens, mask=mask))

In [8]:
print(len(datasets['train']))
print(len(datasets['dev']))
print(len(datasets['test']))
print(datasets['train'][0])
print("____________________________________")
print(len(datasets['train'][0])) # dialogue, tokens, mask 총 3개 ㅇㅋ

482
60
61
TextDataExample(dialogue=['throat a bit sore and want to get a good imune booster, especially in light of the virus. please advise. have not been in contact with nyone with the virus.', "during this pandemic. throat pain can be from a strep throat infection (antibiotics needed), a cold or influenza or other virus, or from some other cause such as allergies or irritants. usually, a person sees the doctor (call first) if the sore throat is bothersome, recurrent, or doesn't go away quickly. covid-19 infections tend to have cough, whereas strep throat usually lacks cough but has more throat pain. (3/21/20)"], tokens=[26110, 265, 257, 1643, 19597, 290, 765, 284, 651, 257, 922, 545, 1726, 30430, 11, 2592, 287, 1657, 286, 262, 9471, 13, 3387, 18595, 13, 423, 407, 587, 287, 2800, 351, 299, 88, 505, 351, 262, 9471, 13, 50256, 42122, 428, 19798, 5314, 13, 13589, 2356, 460, 307, 422, 257, 1937, 79, 13589, 10280, 357, 415, 571, 18296, 2622, 828, 257, 4692, 393, 29491, 393, 584, 9471, 11,

### finetuning training

In [10]:
import torch
from transformers import AutoModelForCausalLM

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = AutoModelForCausalLM.from_pretrained(
                f"microsoft/DialoGPT-{model_size}").to(device)


In [10]:
from transformers import AdamW, get_linear_schedule_with_warmup

n_epochs = 10
batch_size = 5
WARMUP_PROPORTION = 0.05 

train_steps = n_epochs * (len(datasets['train']) // batch_size + 1)
warmup_steps = int(train_steps * WARMUP_PROPORTION) # learning rate 조절하는거래

lr = 4e-5
adam_epsilon = 1e-8
weight_decay = 0.01

# get_optimizer  
no_decay = ["bias", "LayerNorm.weight"]
optimizer_grouped_parameters = [
    {"params": [p for n, p in model.named_parameters() # parameter 호출
                if not any(nd in n for nd in no_decay)],
     "weight_decay": weight_decay},
    {"params": [p for n, p in model.named_parameters()
                if any(nd in n for nd in no_decay)],
     "weight_decay": 0.0}]
optimizer = torch.optim.AdamW(
    optimizer_grouped_parameters, lr=lr, eps=adam_epsilon)

lr_scheduler = get_linear_schedule_with_warmup(
    optimizer, num_warmup_steps=warmup_steps,
    num_training_steps=train_steps)

In [11]:
import torch.nn
def get_loss(example):
    inputs = torch.tensor([example.tokens]).to(device)
    logits = model(inputs)[0] # 모델아웃풋의 keys() 는 odict_keys(['logits', 'past_key_values'])

    # Shift so that tokens < n predict n
    shift_logits = logits[:, :-1].contiguous() # 마지막꺼 하나 뗌
    shift_labels = inputs[:, 1:].contiguous() # 처음꺼하나 뗌 
    shift_masks = torch.tensor(
        example.mask[1:], dtype=torch.float).to(device)

    loss_fn = torch.nn.CrossEntropyLoss(reduction='none')
    loss = loss_fn(
        input=shift_logits.view(-1, shift_logits.size(-1)),
        target=shift_labels.view(-1))

    return torch.sum(loss * shift_masks) / torch.sum(shift_masks)

In [12]:
import random
from tqdm import tqdm

train_dataset = datasets['train'] 
for epoch in range(n_epochs):
    model.train()
    random.shuffle(train_dataset)
    for i in tqdm(range(0,len(train_dataset),batch_size),# iterable
                  ncols = 80 , #진행바 컬럼길이
                  desc = 'Training_Epoch'  #진행률 앞쪽 출력문장
                 ):
        batch = train_dataset[i:i+batch_size]
        optimizer.zero_grad()
        #'''
        #한번의 학습이 완료되어지면(즉, 한 batch의 Iteration이 끝나면), 
        #gradients를 항상 0으로 만들어 주어야 합니다.
        #'''
        for example in batch:
            loss = get_loss(example)/ batch_size
            loss.backward() # loss를 미분(gradient 계산)
                #'''
                #loss = 2 *w
                #loss.backward()
                #print(w.grad) 하면 계산값 2가 출력됨 
                #'''
        optimizer.step()
        lr_scheduler.step()     
        # dev dataset을 이용해서 evaluation을 하면서 
        #best model등을저장하기 추가해야됨
        

Training_Epoch: 100%|███████████████████████████| 97/97 [00:37<00:00,  2.56it/s]


## save & eval

In [13]:
torch.save(model.state_dict(), 'FT_DialoGPT_covid.pt')

In [11]:
## finetuning 된거 불러오기
model.load_state_dict(torch.load('FT_DialoGPT_covid.pt'))
model.eval()

## 비교를 위해 pretrained 된것도 불러오기. 
pretrained_model = AutoModelForCausalLM.from_pretrained(
                f"microsoft/DialoGPT-{model_size}").to(device)
pretrained_model.eval()

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (1): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dro

In [12]:
test_dialogues = load_data('test')
test_dataset = datasets['test']
model.eval()
loss_list =[]
for example in test_dataset: 
    with torch.no_grad():
        loss = get_loss(example)
    loss_list.append(loss.item())
test_loss = sum(loss_list)/len(loss_list)
print(f'Test_loss:{test_loss}')

NameError: name 'get_loss' is not defined

In [13]:
def text_generate(fp_model,chat_history):
        history_ids = []
        for sent in chat_history:
            history_ids.extend(
                tokenizer.encode(sent + tokenizer.eos_token))
        history_ids = torch.tensor([history_ids]).to(device)

        generated_ids = fp_model.generate(
            history_ids,
            num_beams=10,
            length_penalty=2.0,
            max_length=min(1024, history_ids.shape[-1] + 200),
            min_length=history_ids.shape[-1] + 50,
            no_repeat_ngram_size=3,
            pad_token_id=tokenizer.eos_token_id,
        )

        return tokenizer.decode(
            generated_ids[0, history_ids.shape[-1]:], skip_special_tokens=True)

In [14]:
for dialogue in test_dialogues[:2]:
    if len(dialogue) %2 ==1 :
        dialogue  = dialogue[:-1]
    input = dialogue[:-1]
    target = cleantext(dialogue[-1])
    
    generated_text_finetuned = cleantext(text_generate(model, input))
    generated_text_pretrained = cleantext(text_generate(pretrained_model,input))
    
    print("[HISTORY]")
    for i, utterance in enumerate(dialogue[:-1]):
        if i % 2 == 0:
            print(f'Patient: {utterance}')
        else:
            print(f'Doctor: {utterance}')
    print(f'\nGROUND TRUTH:\n{target}')
    print(f'\nGENERATION_finetuned:\n{generated_text_finetuned}')
    print(f'\nGENERATION_pretrained:\n{generated_text_pretrained}')
    

A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


[HISTORY]
Patient: i have all the symptoms except fever, i went to medicross and dr said i can get tested if i want to i'm not sure if i should. she gave me antibiotics klacid xl 500mg, she said i can take it if i feel worse i'm worried it will make immune system bad?

GROUND TRUTH:
in brief: antibiotic i don't recommend antibiotics for a simple viral upper respiratory tract infection unless examination revealed signs of acute bronchitis or sinusitis. they are not effective for viral infections like covid 19 with no bacterial lung involvement either. if you've been exposed to someone with covid 19 or or if you or someone you were exposed to travelled to a region where it was endemic, get tested would you like to video or text chat with me?

GENERATION_finetuned:
in brief: yes you should definitely go to a doctor. would you like to video or text chat with me? i have no idea if you have access to a telephonically or telephonic consult, but i would be happy to help you out. thanks for you

A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


[HISTORY]
Patient: will my mask from sherwin williams paint store with filters protect me from corona virus along with paint fumes?

GROUND TRUTH:
in brief: maybe such a mask helps protect others from any respiratory material you exhale or cough but does not filter out the virus. only high end medical & industrial masks (p95/n95)would filter that. your best protection is frequent hand washing and not touching your face/mouth/nose with contaminated fingers., would you like to video or text chat with me?

GENERATION_finetuned:
in brief: no it won't protect you from coronavirus. would you like to video or text chat with me? i have no idea what you are trying to communicate with me, but i am here for you right now. let me know if i can assist you further. thanks for your question on healthcare magic. i will be happy to help you with any further questions. i have answered your query thoroughly. regards, dr.jolanda

GENERATION_pretrained:
if you have a mask and a respirator, you should be fi

In [14]:
train_dialogues = load_data('train')

In [18]:
for i in train_dialogues:
    if len(i)>2:
        print(i)
        print(len(i))

['hello doctor, last night i was getting chills, feeling more cold than usual and lightheaded and a lot of burping. maybe like every 30 minutes or less or so feel more chills running down my body and chest feeling bit weird like i am starting having trouble breathing then goes back to normal and repeats, with weird feeling like chills down my left and right lungs or left and right upper chest. also, my heart was pumping fast. also, some minor coughs were there since seven days ago, still here. i have white mucus and have not gotten yellow yet. i took medicines yesterday but today i got severe cold and flu medicine with a pain reliever, the chills did not go away. then today, i called the doctor on the phone and told him what happen last night and the same thing happened this morning too. i had minor coughs, feeling lightheaded, feel like maybe cannot breathe or something, and a lot of burping. i told him the burping issue was going on for at least two years, but somehow this time i am 

In [1]:
DISCRIMINATOR_MODELS_PARAMS = {
    "sentiment": {
        "url": "symptom -_classifier_head_epoch_106.pt",
        "class_size": 4, 
        "embed_size": 1024, 
        "class_vocab": {'chest_pain': 0, 'sore_throat': 1, 'cough': 2, 'fever': 3},
        "default_class": 0,  
        "pretrained_model": "dialogpt",
    }
}

In [3]:
set(DISCRIMINATOR_MODELS_PARAMS["sentiment"]["class_vocab"].values())

{0, 1, 2, 3}

In [16]:
test_dialogues[0]

["i have all the symptoms except fever, i went to medicross and dr said i can get tested if i want to i'm not sure if i should. she gave me antibiotics klacid xl 500mg, she said i can take it if i feel worse i'm worried it will make immune system bad?",
 "in brief: antibiotic i don't recommend antibiotics for a simple viral upper respiratory tract infection unless examination revealed signs of acute bronchitis or sinusitis. they are not effective for viral infections like covid 19 with no bacterial lung involvement either. if you've been exposed to someone with covid 19 or or if you or someone you were exposed to travelled to a region where it was endemic, get tested would you like to video or text chat with me?"]

## dailydialog dataset


In [1]:
import numpy as np
import tempfile
from datasets import load_dataset
from transformers import GPT2Tokenizer, GPT2LMHeadModel, TrainingArguments, Trainer

<frozen importlib._bootstrap>:219: RuntimeWarning: pyarrow._fs.FileInfo size changed, may indicate binary incompatibility. Expected 64 from C header, got 88 from PyObject
<frozen importlib._bootstrap>:219: RuntimeWarning: pyarrow._fs.FileSelector size changed, may indicate binary incompatibility. Expected 48 from C header, got 72 from PyObject



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please submit your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
CUDA SETUP: CUDA runtime path found: /home/wooseok/miniconda3/envs/mh/lib/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 6.1
CUDA SETUP: Detected CUDA version 113
CUDA SETUP: Loading binary /home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/libbitsandbytes_cuda113_nocublaslt.so...


/home/wooseok/miniconda3/envs/mh/lib/python3.8/site-packages/bitsandbytes/cuda_setup/main.py:136: UserWarning: WARNING: Compute capability < 7.5 detected! Only slow 8-bit matmul is supported for your GPU!
  warn(msg)


In [2]:
# Load the DailyDialog dataset
dataset = load_dataset('daily_dialog')

# Concatenate all utterances within a dialogue and map to 'dialog' key
def concatenate_utterances(example):
    example['dialog'] = " ".join(example['dialog'])
    return example

# Apply the function to all examples in the dataset
dataset = dataset.map(concatenate_utterances)

Found cached dataset daily_dialog (/home/wooseok/.cache/huggingface/datasets/daily_dialog/default/1.0.0/1d0a58c7f2a4dab5ed9d01dbde8e55e0058e589ab81fce5c2df929ea810eabcd)


  0%|          | 0/3 [00:00<?, ?it/s]

Loading cached processed dataset at /home/wooseok/.cache/huggingface/datasets/daily_dialog/default/1.0.0/1d0a58c7f2a4dab5ed9d01dbde8e55e0058e589ab81fce5c2df929ea810eabcd/cache-0a653ffec771cdaf.arrow
Loading cached processed dataset at /home/wooseok/.cache/huggingface/datasets/daily_dialog/default/1.0.0/1d0a58c7f2a4dab5ed9d01dbde8e55e0058e589ab81fce5c2df929ea810eabcd/cache-152cea1164dfe36f.arrow
Loading cached processed dataset at /home/wooseok/.cache/huggingface/datasets/daily_dialog/default/1.0.0/1d0a58c7f2a4dab5ed9d01dbde8e55e0058e589ab81fce5c2df929ea810eabcd/cache-7c0e92d4e27ffb03.arrow


In [4]:
tokenizer = GPT2Tokenizer.from_pretrained('microsoft/DialoGPT-medium')
tokenizer.pad_token = tokenizer.eos_token
def encode(examples):
    encoded = tokenizer(examples['dialog'], truncation=True, padding='max_length', max_length=128)
    encoded['labels'] = encoded['input_ids'][:]
    return encoded

encoded_dataset = dataset.map(encode, batched=True)

Map:   0%|          | 0/11118 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [7]:
encoded_dataset['train'][0]

{'dialog': "Say , Jim , how about going for a few beers after dinner ?   You know that is tempting but is really not good for our fitness .   What do you mean ? It will help us to relax .   Do you really think so ? I don't . It will just make us fat and act silly . Remember last time ?   I guess you are right.But what shall we do ? I don't feel like sitting at home .   I suggest a walk over to the gym where we can play singsong and meet some of our friends .   That's a good idea . I hear Mary and Sally often go there to play pingpong.Perhaps we can make a foursome with them .   Sounds great to me ! If they are willing , we could ask them to go dancing with us.That is excellent exercise and fun , too .   Good.Let ' s go now .   All right . ",
 'act': [3, 4, 2, 2, 2, 3, 4, 1, 3, 4],
 'emotion': [0, 0, 0, 0, 0, 0, 4, 4, 4, 4],
 'input_ids': [25515,
  837,
  5395,
  837,
  703,
  546,
  1016,
  329,
  257,
  1178,
  16800,
  706,
  8073,
  5633,
  220,
  220,
  921,
  760,
  326,
  318,
  